In [17]:
import os
import json
import logging
import pandas as pd
import folium
from datetime import datetime
from datetime import timedelta


class RouteAnalyzer:
    def __init__(self, root_folder):
        self.root_folder = root_folder
        self.setup_logging()
    
    def load_data(self, folder_path, data_type):
        data_files = [file for file in os.listdir(folder_path) if data_type in file and file.endswith('.json')]
        if not data_files:
            logging.warning(f"No {data_type} file found in {folder_path}")
            return None
            
        with open(os.path.join(folder_path, data_files[0]), 'r') as f:
            data = json.load(f)
        logging.info(f"Loaded {data_type} data from {folder_path}")
        return data
             
    
    def setup_logging(self):
        logging.basicConfig(level=logging.INFO)
    
    def load_json_data(self, json_path):
        """
        Loads data from a given JSON path.
        """
        with open(json_path, 'r') as file:
            data = json.load(file)
        return data

    def load_data_for_folder(self, folder_path):
        """
        Loads GetSolution and ResequenceSolution data from a specified folder path.
        """
        get_solution_files = [file for file in os.listdir(folder_path) if "GetSolution" in file and file.endswith('.json')]
        resequence_solution_files = [file for file in os.listdir(folder_path) if "ResequenceSolution" in file and file.endswith('.json')]
        # Load GetSolution data
        get_solution_data = self.load_json_data(os.path.join(folder_path, get_solution_files[0])) if get_solution_files else None
        
        # Handle ResequenceSolution data based on the number of files detected
        if len(resequence_solution_files) == 0:
            logging.warning(f"No ResequenceSolution file found in {folder_path}")
            resequence_solution_data = None
        elif len(resequence_solution_files) == 1:
            resequence_solution_data = self.load_json_data(os.path.join(folder_path, resequence_solution_files[0]))
        else:
            # Handle the case where there are multiple ResequenceSolution files
            logging.warning(f"Unexpected number of ResequenceSolution files found in {folder_path}. Please check.")
            resequence_solution_data = None  # Or choose one based on some criteria if needed
            
        # Logging
        if get_solution_data:
            logging.info(f"Loaded GetSolution data from {folder_path}")
        else:
            logging.warning(f"No GetSolution file found in {folder_path}")
            
        if resequence_solution_data:
            logging.info(f"Loaded ResequenceSolution data from {folder_path}")
            

            
        return get_solution_data, resequence_solution_data
    

    def extract_metrics(self, data):
        """
        Extracts metrics like distance and journey time for each job.
        """
        metrics = {}
        for route in data['RouteDetails']:
            job_id = route['JobId']
            metrics[job_id] = {
                'Total Distance': route.get('Distance', None),
                'Total Time': route.get('JourneyTime', None)
            }
        logging.info("Metrics extracted.")
        return metrics

    def compare_metrics(self, original_metrics, final_metrics):
        """
        Compares metrics between GetSolution and ResequenceSolution.
        """
        changes = {}
        for job_id, original_values in original_metrics.items():
            final_values = final_metrics.get(job_id, {})
            changes[job_id] = {}
            
            for metric, original_value in original_values.items():
                final_value = final_values.get(metric, None)
                if original_value != final_value:
                    changes[job_id][metric] = {
                        'Original': original_value,
                        'Final': final_value
                    }
        logging.info("Metrics compared.")
        return changes

    def identify_job_changes(self, get_solution_metrics, resequence_solution_metrics):
        """
        Identifies added and removed jobs.
        """
        get_solution_job_ids = set(get_solution_metrics.keys())
        resequence_solution_job_ids = set(resequence_solution_metrics.keys())
        
        added_jobs = resequence_solution_job_ids - get_solution_job_ids
        removed_jobs = get_solution_job_ids - resequence_solution_job_ids
        
        logging.info(f"Added jobs: {len(added_jobs)}, Removed jobs: {len(removed_jobs)}")
        return added_jobs, removed_jobs
    
    def generate_summary_dataframe(self, get_solution_data, reseq_solution_data):
        """
        Generates a summary DataFrame comparing GetSolution and ResequenceSolution.
        """
        # Extract metrics
        get_solution_metrics = self.extract_metrics(get_solution_data)
        reseq_solution_metrics = self.extract_metrics(reseq_solution_data)

        # Extract aggregated metrics for each solution
        total_distance_get_solution = sum([metric['Total Distance'] for metric in get_solution_metrics.values()])
        total_distance_reseq_solution = sum([metric['Total Distance'] for metric in reseq_solution_metrics.values()])
        
        total_time_get_solution = sum((self.str_to_timedelta(metric['Total Time']) for metric in get_solution_metrics.values()), timedelta())
        total_time_reseq_solution = sum((self.str_to_timedelta(metric['Total Time']) for metric in reseq_solution_metrics.values()), timedelta())


        # Create the summary DataFrame
        summary_df = pd.DataFrame({
            'Metric': ['Total Distance (km)', 'Total Time'],
            'GetSolution': [total_distance_get_solution, total_time_get_solution],
            'ResequenceSolution': [total_distance_reseq_solution, total_time_reseq_solution]
        })

        summary_df['Delta'] = summary_df['ResequenceSolution'] - summary_df['GetSolution']
        return summary_df

    def str_to_timedelta(self, time_str):
        """
        Converts a time string in the format "HhMmSs" to a timedelta object.
        """
        try:
            if 'h' in time_str and 'm' in time_str:
                hours, minutes, seconds = map(int, [
                    time_str.split('h')[0], 
                    time_str.split('h')[1].split('m')[0], 
                    time_str.split('m')[1].split('s')[0]
                ])
            else:
                hours, minutes, seconds = map(int, time_str.split(':'))
                
            return timedelta(hours=hours, minutes=minutes, seconds=seconds)
        except Exception as e:
            print(f"Error converting '{time_str}' to timedelta: {e}. Defaulting to 0h0m0s.")
            return timedelta(hours=0, minutes=0, seconds=0)
                
                
                
                
            
    
    def visualize_route(self, route_details, vehicle_id, color):
        coords = [(job['Latitude'], job['Longitude']) for job in route_details if job['VehicleId'] == vehicle_id]
        
        # Debugging statements
        print(f"Data for {vehicle_id}: {route_details[:5]}")  # print the first 5 entries for brevity
        print(f"Number of stops for {vehicle_id}: {len(coords)}")
        

        if not coords:
            print(f"No route data found for {vehicle_id}.")
            return None
        
        average_latitude = sum(coord[0] for coord in coords) / len(coords)
        average_longitude = sum(coord[1] for coord in coords) / len(coords)
        

        route_map = folium.Map(location=[average_latitude, average_longitude], zoom_start=12)
        
        for idx, (lat, lon) in enumerate(coords):
            folium.Marker([lat, lon], popup=f"Stop {idx+1}").add_to(route_map)
        folium.PolyLine(coords, color=color).add_to(route_map)
        
        return route_map

    def save_route_visualization(self, get_solution_data, reseq_solution_data, vehicle_id, output_folder):
        """
        Saves the route visualization maps for the specified vehicle.
        """
        map_get_solution = self.visualize_route(get_solution_data['RouteDetails'], vehicle_id, 'blue')
        map_reseq_solution = self.visualize_route(reseq_solution_data['RouteDetails'], vehicle_id, 'red')
        
        # Debugging: Check if both routes are the same
        if get_solution_data['RouteDetails'] == reseq_solution_data['RouteDetails']:
            print(f"Warning: Routes for {vehicle_id} in get_solution and reseq_solution are identical!")
            

        timestamp = datetime.now().strftime("%Y_%m_%d_%H_%M_%S")
        
        if map_get_solution:
            map_get_solution.save(os.path.join(output_folder, f"map_get_solution_{vehicle_id}_{timestamp}.html"))
        if map_reseq_solution:
            map_reseq_solution.save(os.path.join(output_folder, f"map_reseq_solution_{vehicle_id}_{timestamp}.html"))
            

        print(f"Saved route visualizations for {vehicle_id} in {output_folder}")
        
    
    def calculate_duty_time(self, route_details):
        total_duty_time = timedelta()
        for route in route_details:
            service_time = route.get('ServiceTime', "0h0m0s")
            wait_time = route.get('WaitTime', "0h0m0s")
            total_duty_time += self.str_to_timedelta(service_time) + self.str_to_timedelta(wait_time)
        return total_duty_time

    def count_vehicles(self, route_details):
        return len(set(route['VehicleId'] for route in route_details))

    def calculate_delay_time(self, route_details):
        delay_dict = {}
        for route in route_details:
            vehicle_id = route['VehicleId']
            delay_time = route.get('DelayTime', "0h0m0s")
            delay_dict[vehicle_id] = delay_dict.get(vehicle_id, timedelta()) + self.str_to_timedelta(delay_time)
        return delay_dict

    def count_job_ids(self, route_details):
        return len(set(route['JobId'] for route in route_details))

    def list_vehicle_ids(self, route_details):
        return list(set(route['VehicleId'] for route in route_details))

    def calculate_time_difference(self, start, end):
        FMT = '%H:%M:%S'
        tdelta = datetime.strptime(end, FMT) - datetime.strptime(start, FMT)
        return str(tdelta)
    
    def calculate_number_of_stops(self, route_details):
        """
        Calculates the number of stops based on unique latitude and longitude pairs.
        """
        stops_coordinates = set()
        for route in route_details:
            lat = route['Latitude']
            lon = route['Longitude']
            stops_coordinates.add((lat, lon))
        return len(stops_coordinates)

    def generate_summary_dataframe(self, get_solution_data, reseq_solution_data):
        total_distance_get_solution = sum([metric['Total Distance'] for metric in self.extract_metrics(get_solution_data).values()])
        total_distance_reseq_solution = sum([metric['Total Distance'] for metric in self.extract_metrics(reseq_solution_data).values()])
        
        total_time_get_solution = sum((self.str_to_timedelta(metric['Total Time']) for metric in self.extract_metrics(get_solution_data).values()), timedelta())
        total_time_reseq_solution = sum((self.str_to_timedelta(metric['Total Time']) for metric in self.extract_metrics(reseq_solution_data).values()), timedelta())

        total_duty_time_get_solution = self.calculate_duty_time(get_solution_data['RouteDetails'])
        total_duty_time_reseq_solution = self.calculate_duty_time(reseq_solution_data['RouteDetails'])
        
        num_vehicles_get_solution = self.count_vehicles(get_solution_data['RouteDetails'])
        num_vehicles_reseq_solution = self.count_vehicles(reseq_solution_data['RouteDetails'])
        
        delay_time_get_solution = self.calculate_delay_time(get_solution_data['RouteDetails'])
        delay_time_reseq_solution = self.calculate_delay_time(reseq_solution_data['RouteDetails'])
        
        num_jobs_get_solution = self.count_job_ids(get_solution_data['RouteDetails'])
        num_jobs_reseq_solution = self.count_job_ids(reseq_solution_data['RouteDetails'])
        
        violations_get_solution = get_solution_data.get('RouteViolations', [])
        violations_reseq_solution = reseq_solution_data.get('RouteViolations', [])
        
        vehicle_ids_get_solution = self.list_vehicle_ids(get_solution_data['RouteDetails'])
        vehicle_ids_reseq_solution = self.list_vehicle_ids(reseq_solution_data['RouteDetails'])
        
        num_stops_get_solution = self.calculate_number_of_stops(get_solution_data['RouteDetails'])
        num_stops_reseq_solution = self.calculate_number_of_stops(reseq_solution_data['RouteDetails'])

        summary_df = pd.DataFrame({
            'Metric': [
                'Total Distance (km)', 
                'Total Time', 
                'Duty Time', 
                'Number of Vehicles Used',
                'Delay Time',
                'Number of JobIds',
                'Violations',
                'List of VehicleIds',
                'Number of Stops'
            ],
            
            'GetSolution': [
                total_distance_get_solution, 
                total_time_get_solution, 
                total_duty_time_get_solution, 
                num_vehicles_get_solution,
                delay_time_get_solution,
                num_jobs_get_solution,
                violations_get_solution,
                vehicle_ids_get_solution,
                num_stops_get_solution
            ],
            'ResequenceSolution': [
                total_distance_reseq_solution, 
                total_time_reseq_solution,
                total_duty_time_reseq_solution,
                num_vehicles_reseq_solution,
                delay_time_reseq_solution,
                num_jobs_reseq_solution,
                violations_reseq_solution,
                vehicle_ids_reseq_solution,
                num_stops_reseq_solution
            ]
        })

        summary_df['Delta'] = summary_df.apply(lambda row: row['ResequenceSolution'] - row['GetSolution'] if isinstance(row['GetSolution'], (int, float)) else None, axis=1)

        # Calculate Delta for time values
        for index, row in summary_df.iterrows():
            if isinstance(row['GetSolution'], str) and ':' in row['GetSolution']:
                summary_df.loc[index, 'Delta'] = calculate_time_difference(row['GetSolution'], row['ResequenceSolution'])
            return summary_df

class EnhancedRouteAnalyzer(RouteAnalyzer):
    def load_data_for_folder(self, folder_path):
        """
        Enhanced method to load all GetSolution and ResequenceSolution data from a specified folder path.
        Returns a list of data for each file type.
        """
        # Find GetSolution and ResequenceSolution files
        get_solution_files = sorted([file for file in os.listdir(folder_path) if "GetSolution" in file and file.endswith('.json')])
        resequence_solution_files = sorted([file for file in os.listdir(folder_path) if "ResequenceSolution" in file and file.endswith('.json')])
        
        # If there are more than 6 ResequenceSolution files, return None
        if len(resequence_solution_files) > 6:
            logging.warning(f"Skipping folder {folder_path} as it contains more than 6 ResequenceSolution files.")
            return None, None
            
        
        # Load data for each file
        get_solution_data_list = [self.load_json_data(os.path.join(folder_path, file)) for file in get_solution_files]
        resequence_solution_data_list = [self.load_json_data(os.path.join(folder_path, file)) for file in resequence_solution_files]
        
        # Logging
        if get_solution_data_list:
            logging.info(f"Loaded {len(get_solution_data_list)} GetSolution files from {folder_path}")
        else:
            logging.warning(f"No GetSolution file found in {folder_path}")

        if resequence_solution_data_list:
            logging.info(f"Loaded {len(resequence_solution_data_list)} ResequenceSolution files from {folder_path}")
        else:
            logging.warning(f"No ResequenceSolution file found in {folder_path}")
            
        return get_solution_data_list, resequence_solution_data_list
    
    

    def select_data(self, data_list, file_type):
        """
        If there are multiple files of a type (GetSolution/ResequenceSolution), this method prompts the user 
        to select which one to process or to aggregate all.
        """
        # If there's no file, return None
        if len(data_list) == 0:
            logging.warning(f"No {file_type} files available for selection.")
            logging.info(f"Returning None from select_data due to no {file_type} files.")
            return None
            
        
    
        # If there's only one file, return it
        if len(data_list) == 1:
            return data_list[0]
        
        # If there are multiple files, prompt the user
        print(f"Multiple {file_type} files detected:")
        for idx, data in enumerate(data_list, start=1):
            print(f"{idx}. {data['Filename'] if 'Filename' in data else 'Unknown file'}")
            
        while True:
            choice = input(f"Choose a number (1-{len(data_list)}) to process a specific {file_type} file, or 'all' to aggregate data: ").strip().lower()
            if choice == 'all':
               
                aggregated_data = {}
                for data in data_list:
                    for key, value in data.items():
                        if key not in aggregated_data:
                            aggregated_data[key] = value
                        else:
                            
                            if isinstance(value, list):
                                aggregated_data[key].extend(value)
                return aggregated_data
            elif choice.isdigit() and 1 <= int(choice) <= len(data_list):
                return data_list[int(choice) - 1]
            else:
                print(f"Invalid choice. Please select a number between 1 and {len(data_list)} or 'all'.")
        


    def visualize_combined_routes(self, route_data_list, color_list):
        """
        Visualizes multiple routes on the same map.
        
        Parameters:
        - route_data_list: A list of route details.
        - color_list: A list of colors corresponding to each route.
        """
        if len(route_data_list) != len(color_list):
            print("Mismatch between number of routes and colors.")
            return None
        
        # Initialize map with the coordinates from the first route
        coords = [(job['Latitude'], job['Longitude']) for job in route_data_list[0]]
        if not coords:
            print("No route data found.")
            return None
        
        average_latitude = sum(coord[0] for coord in coords) / len(coords)
        average_longitude = sum(coord[1] for coord in coords) / len(coords)
        
        route_map = folium.Map(location=[average_latitude, average_longitude], zoom_start=12)
        
        for route_details, color in zip(route_data_list, color_list):
            coords = [(job['Latitude'], job['Longitude']) for job in route_details]
            for idx, (lat, lon) in enumerate(coords):
                folium.Marker([lat, lon], popup=f"Stop {idx+1}").add_to(route_map)
            folium.PolyLine(coords, color=color).add_to(route_map)
        
        return route_map        
                


    @staticmethod
    def extract_job_info(data):
        job_info = {}
        for route in data['RouteDetails']:
            job_id = route['JobId']
            coords = (route['Latitude'], route['Longitude'])
            job_info[job_id] = coords
        return job_info

    @staticmethod
    def compare_data(get_solution_data, reseq_solution_data):
        get_solution_jobs = EnhancedRouteAnalyzer.extract_job_info(get_solution_data)
        reseq_solution_jobs = EnhancedRouteAnalyzer.extract_job_info(reseq_solution_data)

        # Identify jobs that are unique to GETSOLUTION and ResequenceSolution
        unique_to_get_solution = set(get_solution_jobs.keys()) - set(reseq_solution_jobs.keys())
        unique_to_reseq_solution = set(reseq_solution_jobs.keys()) - set(get_solution_jobs.keys())

        # Identify jobs that have been relocated in ResequenceSolution
        relocated_jobs = set()
        for job_id in get_solution_jobs:
            if job_id in reseq_solution_jobs and get_solution_jobs[job_id] != reseq_solution_jobs[job_id]:
                relocated_jobs.add(job_id)

        return unique_to_get_solution, unique_to_reseq_solution, relocated_jobs




    def analyze_differences(self, get_solution_data, reseq_solution_data):
        # Extracting job IDs from both solutions
        get_solution_jobs = {job['JobId']: (job['Latitude'], job['Longitude']) for job in get_solution_data['RouteDetails']}
        reseq_solution_jobs = {job['JobId']: (job['Latitude'], job['Longitude']) for job in reseq_solution_data['RouteDetails']}

        # Identifying job IDs unique to each solution
        unique_to_get_solution = set(get_solution_jobs.keys()) - set(reseq_solution_jobs.keys())
        unique_to_reseq_solution = set(reseq_solution_jobs.keys()) - set(get_solution_jobs.keys())

        # Identifying jobs that are present in both but have different coordinates
        relocated_jobs = {job_id: (get_solution_jobs[job_id], reseq_solution_jobs[job_id]) 
                          for job_id in get_solution_jobs 
                          if job_id in reseq_solution_jobs and get_solution_jobs[job_id] != reseq_solution_jobs[job_id]}

        # Identifying jobs that are present in both and have the same coordinates
        retained_jobs = {job_id: get_solution_jobs[job_id]
                        for job_id in get_solution_jobs 
                        if job_id in reseq_solution_jobs and get_solution_jobs[job_id] == reseq_solution_jobs[job_id]}

        print(f"Jobs unique to GETSOLUTION: {unique_to_get_solution}")
        print(f"Jobs unique to ResequenceSolution: {unique_to_reseq_solution}")
        print(f"Jobs that have been relocated in ResequenceSolution (with old and new coordinates): {relocated_jobs}")
        print(f"Jobs that were retained in ResequenceSolution (with coordinates): {retained_jobs}")

    


    def visualize_common_jobs_on_map(self, get_solution_data, reseq_solution_data):
        """
        Visualizes common job routes between GetSolution and ResequenceSolution on a map.
        """
        # Extract job IDs and their coordinates from both solutions
        get_solution_jobs = {job['JobId']: (job['Latitude'], job['Longitude']) for job in get_solution_data['RouteDetails']}
        reseq_solution_jobs = {job['JobId']: (job['Latitude'], job['Longitude']) for job in reseq_solution_data['RouteDetails']}

        # Identify job IDs common to both solutions
        common_job_ids = set(get_solution_jobs.keys()).intersection(set(reseq_solution_jobs.keys()))

        # Extract routes for common job IDs
        get_solution_common_route = [get_solution_jobs[job_id] for job_id in common_job_ids]
        reseq_solution_common_route = [reseq_solution_jobs[job_id] for job_id in common_job_ids]

        # Initialize the map with the average coordinates from the common routes
        all_coords = get_solution_common_route + reseq_solution_common_route
        average_latitude = sum(coord[0] for coord in all_coords) / len(all_coords)
        average_longitude = sum(coord[1] for coord in all_coords) / len(all_coords)
        route_map = folium.Map(location=[average_latitude, average_longitude], zoom_start=12)
        
        # Plot the GetSolution route in blue
        folium.PolyLine(get_solution_common_route, color="blue", weight=2.5, opacity=1).add_to(route_map)
        
        # Plot the ResequenceSolution route in red
        folium.PolyLine(reseq_solution_common_route, color="red", weight=2.5, opacity=1).add_to(route_map)

        # Add markers for each job
        for idx, (lat, lon) in enumerate(all_coords):
            folium.Marker([lat, lon], popup=f"Common Stop {idx+1}").add_to(route_map)
        
        return route_map



    def has_order_changed(self, get_solution_data, reseq_solution_data):
        """Check if the order of jobs has changed between GetSolution and ResequenceSolution."""
        # Extract the sequence of job IDs from both solutions
        get_solution_ids = [job['JobId'] for job in get_solution_data['RouteDetails']]
        reseq_solution_ids = [job['JobId'] for job in reseq_solution_data['RouteDetails']]
        
        # Compare the sequences
        if get_solution_ids != reseq_solution_ids:
            return True
        return False

    




In [18]:
def main():
    try:
        logging.basicConfig(level=logging.INFO)
        
        # Define the root folder that contains all the sub-folders
        root_folder = r"C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles"
        output_folder = r"C:\Users\mreth\Desktop\Dissertation\RouteVisualizations3"
        
        if not os.path.exists(output_folder):
            os.makedirs(output_folder)

        analyzer = EnhancedRouteAnalyzer(root_folder)
        all_data = []  # List to hold consolidated data for all folders
        all_summaries = []  # List to hold summary data for all folders
        all_coordinates = []  # List to hold coordinate comparisons for all folders

        for folder_name in os.listdir(root_folder):
            folder_path = os.path.join(root_folder, folder_name)

            if os.path.isdir(folder_path):
                get_solution_data_list, reseq_solution_data_list = analyzer.load_data_for_folder(folder_path)
                
                if get_solution_data_list is None or reseq_solution_data_list is None:
                    logging.warning(f"Data lists not loaded properly for {folder_path}. Skipping...")
                    continue
                
                if reseq_solution_data_list is not None and len(reseq_solution_data_list) > 6:
                    logging.info(f"Skipping folder {folder_name} as it contains more than 6 ResequenceSolution files.")
                    continue
                
                get_solution_data = analyzer.select_data(get_solution_data_list, "GetSolution")
                if get_solution_data is None:
                    logging.warning(f"No selected GetSolution data available for {folder_path}. Skipping...")
                    continue
                    
                reseq_solution_data = analyzer.select_data(reseq_solution_data_list, "ResequenceSolution")
                if reseq_solution_data is None:
                    logging.warning(f"No selected ResequenceSolution data available for {folder_path}. Skipping...")
                    continue
                
                analyzer.analyze_differences(get_solution_data, reseq_solution_data)
                
                changed = analyzer.has_order_changed(get_solution_data, reseq_solution_data)
                if changed:
                    print("The order of jobs has changed in the ResequenceSolution.")
                else:
                    print("The order of jobs remains the same in the ResequenceSolution.")
                
               

                if get_solution_data and reseq_solution_data:
                    summary_df = analyzer.generate_summary_dataframe(get_solution_data, reseq_solution_data)
                    print("\nSummary for folder:", folder_name)
                    print(summary_df)
                    
                    unique_jobs_get, unique_jobs_reseq, relocated_jobs = analyzer.compare_data(get_solution_data, reseq_solution_data)
                    get_solution_jobs = {job['JobId'] for job in get_solution_data['RouteDetails']}
                    reseq_solution_jobs = {job['JobId'] for job in reseq_solution_data['RouteDetails']}
                    retained_jobs = get_solution_jobs & reseq_solution_jobs

                    
                    # Construct the folder_data
                    folder_data = {
                        'Folder Name': folder_name,
                        'Jobs Unique to GETSOLUTION': list(unique_jobs_get),
                        'Jobs Unique to ResequenceSolution': list(unique_jobs_reseq),
                        'Jobs Relocated': list(relocated_jobs),
                        'Jobs Retained': list(retained_jobs),
                        'Order Changed': changed
                    }
                    
                    
                    for index, row in summary_df.iterrows():
                        metric_name_get = f"{row['Metric']} (GetSolution)"
                        metric_name_reseq = f"{row['Metric']} (ResequenceSolution)"
                        metric_name_delta = f"Summary {row['Metric']} (Delta)"
                        folder_data[metric_name_get] = row['GetSolution']   
                        folder_data[metric_name_reseq] = row['ResequenceSolution']
                        # If there's a Delta column in the dataframe, store its value
                        if 'Delta' in summary_df.columns:
                            folder_data[metric_name_delta] = row['Delta']

                    combined_map = analyzer.visualize_combined_routes(
                        [get_solution_data['RouteDetails'], reseq_solution_data['RouteDetails']],
                        ['blue', 'red']
                    )
                    display(combined_map)
                    
                    summary_data = summary_df.to_dict(orient='records')
                    for record in summary_data:
                        record["folder"] = folder_name
                    all_summaries.extend(summary_data)
                    
                    get_coords = [(route['Latitude'], route['Longitude']) for route in get_solution_data['RouteDetails']]
                    reseq_coords = [(route['Latitude'], route['Longitude']) for route in reseq_solution_data['RouteDetails']]
                    
                    print(f"\nCoordinates for folder {folder_name}:")
                    print("GetSolution Coordinates:", get_coords)
                    print("ResequenceSolution Coordinates:", reseq_coords)
                    
                    coord_comparison = {
                        "folder": folder_name,
                        "get_solution_coords": get_coords,
                        "reseq_solution_coords": reseq_coords
                    }
                    all_coordinates.append(coord_comparison)
                    
                    
                
                    # Print the folder_data for the current folder
                    print("\nFolder Data for", folder_name)
                    print("-------------------------------------------------")
                    for key, value in folder_data.items():
                        print(f"{key}: {value}")
                    print("-------------------------------------------------\n")
                    
                    
                all_data.append(folder_data)
        
        pd.DataFrame(all_data).to_csv(os.path.join(output_folder, 'consolidated_data.csv'), index=False)
        pd.DataFrame(all_summaries).to_csv(os.path.join(output_folder, "all_summaries.csv"), index=False)
        pd.DataFrame(all_coordinates).to_csv(os.path.join(output_folder, "all_coordinates.csv"), index=False)

    except Exception as e:
        logging.error(f"An error occurred: {e}")
        import traceback
        traceback.print_exc()

if __name__ == "__main__":
    main()


INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206931
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206932
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206933
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206934
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206936
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mret

Jobs unique to GETSOLUTION: {'D-040523EF79', 'C-040523EF79'}
Jobs unique to ResequenceSolution: set()
Jobs that have been relocated in ResequenceSolution (with old and new coordinates): {}
Jobs that were retained in ResequenceSolution (with coordinates): {'Depot': (-27.423980712890625, 153.0890655517578), 'C-040523EF78': (-27.423980712890625, 153.0890655517578), 'C-040523EF77': (-27.423980712890625, 153.0890655517578), 'C-040523EF91': (-27.423980712890625, 153.0890655517578), 'C-040523EF89': (-27.423980712890625, 153.0890655517578), 'C-040523EF80': (-27.423980712890625, 153.0890655517578), 'C-040523EF76': (-27.423980712890625, 153.0890655517578), 'C-040523EF82': (-27.423980712890625, 153.0890655517578), 'C-040523EF90': (-27.423980712890625, 153.0890655517578), 'C-040523EF84': (-27.423980712890625, 153.0890655517578), 'C-040523EF94': (-27.423980712890625, 153.0890655517578), 'C-040523EF81': (-27.423980712890625, 153.0890655517578), 'C-040523EF88': (-27.423980712890625, 153.0890655517578

INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206952
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206954
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 2 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206955



Coordinates for folder 206951:
GetSolution Coordinates: [(-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.444080352783203, 152.9436492919922), (-27.51542091369629, 152.9539337158203), (-27.58720016479492

INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 2 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\206956


...

Multiple GetSolution files detected:
1. Unknown file
2. Unknown file
Choose a number (1-2) to process a specific GetSolution file, or 'all' to aggregate data: 2


INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208076
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208077
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208078
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208079
INFO:root:Loaded 1 ResequenceSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208079
INFO:root:Metrics extracted.
INFO:root:Metrics extracted.
INFO:root:Metrics extracted.
INFO:root:Metrics extracted.


Jobs unique to GETSOLUTION: {'D-150623EF117', 'C-150623EF117'}
Jobs unique to ResequenceSolution: set()
Jobs that have been relocated in ResequenceSolution (with old and new coordinates): {}
Jobs that were retained in ResequenceSolution (with coordinates): {'Depot': (-27.423980712890625, 153.0890655517578), 'C-150623EF127': (-27.423980712890625, 153.0890655517578), 'C-150623EF130': (-27.423980712890625, 153.0890655517578), 'C-150623EF116': (-27.423980712890625, 153.0890655517578), 'C-150623EF122': (-27.423980712890625, 153.0890655517578), 'C-150623EF129': (-27.423980712890625, 153.0890655517578), 'C-150623EF128': (-27.423980712890625, 153.0890655517578), 'C-150623EF118': (-27.423980712890625, 153.0890655517578), 'C-150623EF115': (-27.423980712890625, 153.0890655517578), 'C-150623EF123': (-27.423980712890625, 153.0890655517578), 'C-150623EF124': (-27.423980712890625, 153.0890655517578), 'C-150623EF125': (-27.423980712890625, 153.0890655517578), 'C-150623EF126': (-27.423980712890625, 153

INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208081
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208082
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208083
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208084
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mreth\Desktop\Dissertation\EncodedFiles\EncodedFiles\208086
INFO:root:Returning None from select_data due to no ResequenceSolution files.
INFO:root:Loaded 1 GetSolution files from C:\Users\mret


Coordinates for folder 208079:
GetSolution Coordinates: [(-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.423980712890625, 153.0890655517578), (-27.391769409179688, 153.0587921142578), (-27.391769409179688, 153.0587921142578), (-27.219900131225586, 153.09397888183594), (-27.22154998779297, 153.1107635498047), (-27.2275905609130